# Trabalho de Banco de Dados (A2) - Estudo da distribuição do Rodoanel nas cidades de São Paulo

Nesse trabalho, nosso objetivo principal é: 
* Dado uma base de dados GeoJson do Rodoanel de São Paulo e outra base de dados GeoJson das cidades de São Paulo, fazer uma visualização das cidades x Rodoanel, para identificar quais são as cidades pela qual o Rodoanel passa. 

## Membros

- Rian Freitas
- Cristiano Larréa

### Bibliotecas Necessárias

In [172]:
#!pip install pymongo
#!pip install folium
#!pip install pandas

## Importando as bibliotecas

In [173]:
import pandas as pd
import json
import os
import pymongo
from pymongo import MongoClient
import folium

## Carregando as duas bases de dados no banco MongoDB

Primeiro, instaciamos o banco de dados e as collections

In [174]:
client = MongoClient('localhost', 27017)
db = client['RodoanelSP']
jsons = db['files']
cidades = db['cidades']

Agora, realizamos o insert das informações nas collections

In [175]:
with open('rodoanel.json', 'r', encoding='UTF-8') as arquivo:
    rodoanel = json.load(arquivo)
query_rodoanel = jsons.insert_one(rodoanel)
with open(os.path.join('geodata-br','geojson','geojs-35-mun.json'), 'r',encoding='UTF-8') as arquivo:
    cities = json.load(arquivo)
for featurecollection in cities['features']:
    query_cities = cidades.insert_one(featurecollection)

Aqui, acessamos o banco de dados para criar outro dicionário (melhor organizado para ser utilizado posteriormente), que será utilizado no Choropleth posteriormente.

In [176]:
cidades_dict = {}
my_dict = cidades.find_one()
my_dict2 = my_dict['features']
for cidade in my_dict2:
    cidades_dict[cidade['properties']['name']] = cidade['geometry']

## Análise

Para criar a visualização, iremos utilizar o Folium. Será criada uma visualização do tipo GeoJson (que irá plotar o trajeto do Rodoanel) e uma Choropleth (que irá plotar as cidades de São Paulo).

In [177]:
m = folium.Map(
    location=[-23.5489, -46.6388],
    zoom_start=10,
)

for cidade in cidades_dict:
    folium.Choropleth(
        geo_data = cidades_dict.get(cidade), name="choropleth", fill_color="red", fill_opacity=0.2).add_to(m)
    
for doc in jsons.find():
    folium.GeoJson(doc.get('features')[0], name="geojson").add_to(m)
    
m